# Content-based recommenders

Content-based recommenders in their recommendations rely purely on the features of users and items. Conceptually it can be expressed as a model of the form (personalized):

<center>
$$
    score \sim (user\_feature\_1, user\_feature\_2, ..., user\_feature\_k, item\_feature_1, item\_feature_2, ..., item\_feature_n)
$$
</center>

or (not personalized)

<center>
$$
    score \sim (item\_feature_1, item\_feature_2, ..., item\_feature_n)
$$
</center>


    + Content-based recommenders do not suffer from the cold-start problem for new items.
    - They do not use information about complex patterns of user-item interactions - what other similar users have already
    discovered and liked.

In [15]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import Markdown, display, HTML
from collections import defaultdict
from sklearn.model_selection import KFold
import time

pd.set_option('display.max_columns', 50)

from evaluation_and_testing.testing import evaluate_train_test_split_explicit
from evaluation_and_testing.testing import evaluate_leave_one_out_explicit
from evaluation_and_testing.testing import evaluate_train_test_split_implicit
from evaluation_and_testing.testing import evaluate_leave_one_out_implicit

# Fix the dying kernel problem (only a problem in some installations - you can remove it, if it works without it)
import os
os.environ['KMP_DUPLICATE_LIB_OK'] = 'True'

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Load the data

In [16]:
ml_ratings_df = pd.read_csv(os.path.join("data", "movielens_small", "ratings.csv")).rename(columns={'userId': 'user_id', 'movieId': 'item_id'})
ml_movies_df = pd.read_csv(os.path.join("data", "movielens_small", "movies.csv")).rename(columns={'movieId': 'item_id'})
ml_df = pd.merge(ml_ratings_df, ml_movies_df, on='item_id')

display(ml_movies_df.head(10))

# Filter the data to reduce the number of movies
seed = 6789
rng = np.random.RandomState(seed=seed)
left_ids = rng.choice(ml_movies_df['item_id'], size=1000, replace=False)

ml_ratings_df = ml_ratings_df.loc[ml_ratings_df['item_id'].isin(left_ids)]
ml_movies_df = ml_movies_df.loc[ml_movies_df['item_id'].isin(left_ids)]
ml_df = ml_df.loc[ml_df['item_id'].isin(left_ids)]

print("Number of left interactions: {}".format(len(ml_ratings_df)))

item_id                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   
5        6                         Heat (1995)   
6        7                      Sabrina (1995)   
7        8                 Tom and Huck (1995)   
8        9                 Sudden Death (1995)   
9       10                    GoldenEye (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy  
5                        Action|Crime|Thriller  
6                               Comedy|Romance  
7                           Adventure|Children  
8                                       Action  
9                    Action|Adventure|Thriller

Number of left interactions: 9692


# Linear Regression Recommender

For every movie we transform its genres into one-hot encoded features and we normalize them, for every user we count percentages for all genres how often do they appear among films watched by the user, we multiply both vectors (for the item and the user) to obtain explanaytory variables, and then we fit a linear regression model to those features and actual ratings.

In [18]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import MultiLabelBinarizer

class LinearRegressionRecommender(object):
    """
    Linear regression recommender class.
    """
    
    def __init__(self):
        """
        Initialize recommender params and variables.
        """
        self.model = None
        self.mlb = None
        self.users_dict = None
        self.user_features = None
    
    def fit(self, interactions_df, users_df, items_df):
        """
        Training of the recommender.
        
        :param pd.DataFrame interactions_df: DataFrame with recorded interactions between users and items 
            defined by user_id, item_id and features of the interaction.
        :param pd.DataFrame users_df: DataFrame with users and their features defined by user_id and the user feature columns.
        :param pd.DataFrame items_df: DataFrame with items and their features defined by item_id and the item feature columns.
        """
        
        # Transform genres to a more code-friendly form
        
        interactions_df = pd.merge(interactions_df, items_df, on='item_id')
        interactions_df = self._transform_genres(interactions_df)
        
        # Prepare user features
        
        users_df = interactions_df[['user_id', 'genres']].copy()
        users_df = users_df.explode('genres')
        users_df['val'] = 1
        users_df = users_df.pivot_table(index='user_id', columns='genres', values='val', aggfunc='count')
        users_df = users_df / users_df.sum(axis=1).values.reshape(-1, 1)
        users_df = users_df.rename_axis(None, axis=1).fillna(0)
        users_df = users_df.add_prefix('user_')
#         display(users_df.head(10))
        
        self.users_dict = users_df.to_dict('index')
        
        self.user_features = users_df.columns.tolist()
        
        interactions_df = interactions_df.merge(users_df, on='user_id')
#         display(interactions_df.head(10))
                
        # Prepare item features
        
        # Transform genres into binary values
        
        self.mlb = MultiLabelBinarizer()
        interactions_df = interactions_df.join(
            pd.DataFrame(self.mlb.fit_transform(interactions_df.pop('genres')),
                         columns=self.mlb.classes_,
                         index=interactions_df.index))
        
        # Normalize the values so that each movie's genres sum up to 1
        
        interactions_df[self.mlb.classes_] = interactions_df[self.mlb.classes_] \
            / interactions_df[self.mlb.classes_].sum(axis=1).values.reshape(-1, 1)
        
#         display(interactions_df.loc[:, self.mlb.classes_].head(10))

        # Prepare input data and fit the model
    
        interactions_df[self.mlb.classes_] = interactions_df[self.mlb.classes_] \
            * interactions_df[self.user_features].values
    
#         display(interactions_df.head(10))
        
        x = interactions_df.loc[:, list(self.mlb.classes_)].values
        y = interactions_df['rating'].values
    
        self.model = LinearRegression().fit(x, y)
    
    def recommend(self, users_df, items_df, n_recommendations=1):
        """
        Serving of recommendations. Scores items in items_df for each user in users_df and returns 
        top n_recommendations for each user.
        
        :param pd.DataFrame users_df: DataFrame with users and their features for which recommendations should be generated.
        :param pd.DataFrame items_df: DataFrame with items and their features which should be scored.
        :param int n_recommendations: Number of recommendations to be returned for each user.
        :return: DataFrame with user_id, item_id and score as columns returning n_recommendations top recommendations 
            for each user.
        :rtype: pd.DataFrame
        """
        
        # Transform the item to be scored into proper features
        
        items_df = items_df.copy()
        items_df = self._transform_genres(items_df)
        
        items_df = items_df.join(
            pd.DataFrame(self.mlb.transform(items_df.pop('genres')),
                         columns=self.mlb.classes_,
                         index=items_df.index))
        
        items_df[self.mlb.classes_] = items_df[self.mlb.classes_] \
            / items_df[self.mlb.classes_].sum(axis=1).values.reshape(-1, 1)

        display(items_df)
        # Score the item
    
        recommendations = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
        
        for ix, user in users_df.iterrows():
            if user['user_id'] in self.users_dict:
                user_df = pd.DataFrame.from_dict({user['user_id']: self.users_dict[user['user_id']]}, orient='index')
            else:
                user_df = pd.DataFrame.from_dict(
                    {user['user_id']: [1 / len(self.user_features)]*len(self.user_features)}, orient='index')
#             display(user_df)
#             display(items_df)
            input_df = items_df.copy()
            input_df[self.mlb.classes_] = items_df[self.mlb.classes_] * user_df.values
#             display(input_df)
            scores = self.model.predict(input_df.loc[:, self.mlb.classes_].values)
    
            chosen_pos = np.argsort(-scores)[:n_recommendations]
        
            user_recommendations = []
            for item_pos in chosen_pos:
                user_recommendations.append(
                    {
                        'user_id': user['user_id'],
                        'item_id': input_df.iloc[item_pos]['item_id'],
                        'score': scores[item_pos]
                    }
                )
                
            user_recommendations = pd.DataFrame(user_recommendations)

            recommendations = pd.concat([recommendations, user_recommendations])

        return recommendations
    
    def _transform_genres(self, df):
        """
        Transforms a string with genres into a list of cleaned genre names.
        
        :param pd.DataFrame df: A DataFrame with 'genres' column.
        """
        df.loc[:, 'genres'] = df['genres'].str.replace("-", "_", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.replace(" ", "_", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.replace("(", "", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.replace(")", "", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.lower()
        df.loc[:, 'genres'] = df['genres'].str.split("|")
        return df

In [19]:
# Quick test of the recommender

lr_recommender = LinearRegressionRecommender()
lr_recommender.fit(ml_ratings_df, None, ml_movies_df)
recommendations = lr_recommender.recommend(pd.DataFrame([[1], [2]], columns=['user_id']), ml_movies_df, 10)

recommendations = pd.merge(recommendations, ml_movies_df, on='item_id', how='left')
display(recommendations)

item_id                               title    action  adventure  \
3           4            Waiting to Exhale (1995)  0.000000       0.00   
11         12  Dracula: Dead and Loving It (1995)  0.000000       0.00   
46         50          Usual Suspects, The (1995)  0.000000       0.00   
66         74                 Bed of Roses (1996)  0.000000       0.00   
70         78          Crossing Guard, The (1995)  0.250000       0.00   
...       ...                                 ...       ...        ...   
9697   184987            A Wrinkle in Time (2018)  0.000000       0.25   
9704   185473                     Blockers (2018)  0.000000       0.00   
9721   189381                     SuperFly (2018)  0.333333       0.00   
9725   190207                         Tilt (2011)  0.000000       0.00   
9727   190213                    John From (2015)  0.000000       0.00   

      animation  children    comedy     crime  documentary     drama  fantasy  \
3           0.0      0.00  0.333333  0.000000          0.0  0.333333     0.00   
11          0.0      0.00  0.500000  0.000000          0.0  0.000000     0.00   
46          0.0      0.00  0.000000  0.333333          0.0  0.000000     0.00   
66          0.0      0.00  0.000000  0.000000          0.0  0.500000     0.00   
70          0.0      0.00  0.000000  0.250000          0.0  0.250000     0.00   
...         ...       ...       ...       ...          ...       ...      ...   
9697        0.0      0.25  0.000000  0.000000          0.0  0.000000     0.25   
9704        0.0      0.00  1.000000  0.000000          0.0  0.000000     0.00   
9721        0.0      0.00  0.000000  0.333333          0.0  0.000000     0.00   
9725        0.0      0.00  0.000000  0.000000          0.0  0.500000     0.00   
9727        0.0      0.00  0.000000  0.000000          0.0  1.000000     0.00   

      film_noir  horror  imax  musical   mystery  no_genres_listed   romance  \
3           0.0     0.0   0.0      0.0  0.000000               0.0  0.333333   
11          0.0     0.5   0.0      0.0  0.000000               0.0  0.000000   
46          0.0     0.0   0.0      0.0  0.333333               0.0  0.000000   
66          0.0     0.0   0.0      0.0  0.000000               0.0  0.500000   
70          0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
...         ...     ...   ...      ...       ...               ...       ...   
9697        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
9704        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
9721        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
9725        0.0     0.0   0.0      0.0  0.000000               0.0  0.500000   
9727        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   

      sci_fi  thriller  war  western  
3       0.00  0.000000  0.0      0.0  
11      0.00  0.000000  0.0      0.0  
46      0.00  0.333333  0.0      0.0  
66      0.00  0.000000  0.0      0.0  
70      0.00  0.250000  0.0      0.0  
...      ...       ...  ...      ...  
9697    0.25  0.000000  0.0      0.0  
9704    0.00  0.000000  0.0      0.0  
9721    0.00  0.333333  0.0      0.0  
9725    0.00  0.000000  0.0      0.0  
9727    0.00  0.000000  0.0      0.0  

[1000 rows x 22 columns]

user_id item_id     score  \
0        1   66335  4.150819   
1        1  160848  4.150819   
2        1   32657  3.817562   
3        1  146028  3.802604   
4        1  147286  3.802604   
5        1     858  3.760289   
6        1    5888  3.760289   
7        1    4239  3.760289   
8        1    5954  3.760289   
9        1    4889  3.760289   
10       2    8656  4.252642   
11       2    1213  4.252642   
12       2   31309  4.252642   
13       2    4139  4.252642   
14       2   37741  4.252642   
15       2   39292  4.252642   
16       2   43912  4.252642   
17       2     858  4.252642   
18       2    5888  4.252642   
19       2   53447  4.252642   

                                                title           genres  
0                   Afro Samurai: Resurrection (2009)        Animation  
1                               The Red Turtle (2016)        Animation  
2   Man Who Planted Trees, The (Homme qui plantait...  Animation|Drama  
3   The Adventures of Sherlock Holmes and Dr. Wats...    Crime|Mystery  
4   The Adventures of Sherlock Holmes and Doctor W...    Crime|Mystery  
5                               Godfather, The (1972)      Crime|Drama  
6                               Brother (Brat) (1997)      Crime|Drama  
7                                         Blow (2001)      Crime|Drama  
8                                    25th Hour (2002)      Crime|Drama  
9                                        Heist (2001)      Crime|Drama  
10  Short Film About Killing, A (Krótki film o zab...      Crime|Drama  
11                                  Goodfellas (1990)      Crime|Drama  
12  Rocco and His Brothers (Rocco e i suoi fratell...      Crime|Drama  
13                               No Man's Land (1987)      Crime|Drama  
14                                      Capote (2005)      Crime|Drama  
15                  Good Night, and Good Luck. (2005)      Crime|Drama  
16                                 Freedomland (2006)      Crime|Drama  
17                              Godfather, The (1972)      Crime|Drama  
18                              Brother (Brat) (1997)      Crime|Drama  
19                               Paranoid Park (2007)      Crime|Drama

### Train-test split test

In [ ]:
lr_recommender = LinearRegressionRecommender()

t0 = time.time()

results = [['LinearRegressionRecommender'] + list(evaluate_train_test_split_explicit(
    lr_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id', 'rating']], ml_movies_df, seed=seed))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'RMSE', 'MRE', 'TRE'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))

item_id               title  action  adventure  animation  children  \
0   3751.0  Chicken Run (2000)     0.0        0.0   0.333333  0.333333   

     comedy  crime  documentary  drama  fantasy  film_noir  horror  imax  \
0  0.333333    0.0          0.0    0.0      0.0        0.0     0.0   0.0   

   musical  mystery  no_genres_listed  romance  sci_fi  thriller  war  western  
0      0.0      0.0               0.0      0.0     0.0       0.0  0.0      0.0

item_id                     title    action  adventure  animation  \
0   7438.0  Kill Bill: Vol. 2 (2004)  0.333333        0.0        0.0   

   children  comedy  crime  documentary     drama  fantasy  film_noir  horror  \
0       0.0     0.0    0.0          0.0  0.333333      0.0        0.0     0.0   

   imax  musical  mystery  no_genres_listed  romance  sci_fi  thriller  war  \
0   0.0      0.0      0.0               0.0      0.0     0.0  0.333333  0.0   

   western  
0      0.0

item_id              title  action  adventure  animation  children  comedy  \
0  91842.0  Contraband (2012)    0.25        0.0        0.0       0.0     0.0   

   crime  documentary  drama  fantasy  film_noir  horror  imax  musical  \
0   0.25          0.0   0.25      0.0        0.0     0.0   0.0      0.0   

   mystery  no_genres_listed  romance  sci_fi  thriller  war  western  
0      0.0               0.0      0.0     0.0      0.25  0.0      0.0

item_id                       title  action  adventure  animation  \
0   1500.0  Grosse Pointe Blank (1997)     0.0        0.0        0.0   

   children    comedy     crime  documentary  drama  fantasy  film_noir  \
0       0.0  0.333333  0.333333          0.0    0.0      0.0        0.0   

   horror  imax  musical  mystery  no_genres_listed   romance  sci_fi  \
0     0.0   0.0      0.0      0.0               0.0  0.333333     0.0   

   thriller  war  western  
0       0.0  0.0      0.0

item_id                     title  action  adventure  animation  children  \
0   1955.0  Kramer vs. Kramer (1979)     0.0        0.0        0.0       0.0   

   comedy  crime  documentary  drama  fantasy  film_noir  horror  imax  \
0     0.0    0.0          0.0    1.0      0.0        0.0     0.0   0.0   

   musical  mystery  no_genres_listed  romance  sci_fi  thriller  war  western  
0      0.0      0.0               0.0      0.0     0.0       0.0  0.0      0.0

...

item_id                  title  action  adventure  animation  children  \
0    858.0  Godfather, The (1972)     0.0        0.0        0.0       0.0   

   comedy  crime  documentary  drama  fantasy  film_noir  horror  imax  \
0     0.0    0.5          0.0    0.5      0.0        0.0     0.0   0.0   

   musical  mystery  no_genres_listed  romance  sci_fi  thriller  war  western  
0      0.0      0.0               0.0      0.0     0.0       0.0  0.0      0.0

item_id                       title  action  adventure  animation  \
0    280.0  Murder in the First (1995)     0.0        0.0        0.0   

   children  comedy  crime  documentary  drama  fantasy  film_noir  horror  \
0       0.0     0.0    0.0          0.0    0.5      0.0        0.0     0.0   

   imax  musical  mystery  no_genres_listed  romance  sci_fi  thriller  war  \
0   0.0      0.0      0.0               0.0      0.0     0.0       0.5  0.0   

   western  
0      0.0

item_id                                              title  action  \
0    750.0  Dr. Strangelove or: How I Learned to Stop Worr...     0.0   

   adventure  animation  children  comedy  crime  documentary  drama  fantasy  \
0        0.0        0.0       0.0     0.5    0.0          0.0    0.0      0.0   

   film_noir  horror  imax  musical  mystery  no_genres_listed  romance  \
0        0.0     0.0   0.0      0.0      0.0               0.0      0.0   

   sci_fi  thriller  war  western  
0     0.0       0.0  0.5      0.0

item_id                title  action  adventure  animation  children  \
0   2502.0  Office Space (1999)     0.0        0.0        0.0       0.0   

   comedy  crime  documentary  drama  fantasy  film_noir  horror  imax  \
0     0.5    0.5          0.0    0.0      0.0        0.0     0.0   0.0   

   musical  mystery  no_genres_listed  romance  sci_fi  thriller  war  western  
0      0.0      0.0               0.0      0.0     0.0       0.0  0.0      0.0

item_id                                title  action  adventure  animation  \
0   3451.0  Guess Who's Coming to Dinner (1967)     0.0        0.0        0.0   

   children  comedy  crime  documentary  drama  fantasy  film_noir  horror  \
0       0.0     0.0    0.0          0.0    1.0      0.0        0.0     0.0   

   imax  musical  mystery  no_genres_listed  romance  sci_fi  thriller  war  \
0   0.0      0.0      0.0               0.0      0.0     0.0       0.0  0.0   

   western  
0      0.0

### Leave-one-out test

In [11]:
lr_recommender = LinearRegressionRecommender()

t0 = time.time()

results = [['LinearRegressionRecommender'] + list(evaluate_leave_one_out_explicit(
    lr_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id', 'rating']], ml_movies_df, seed=seed))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'RMSE', 'MRE', 'TRE'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))

Recommender      RMSE       MRE       TRE
0  LinearRegressionRecommender  1.045415  0.401399  0.242301

Total evaluation time: 36.1777925491333


# TF-IDF Recommender
TF-IDF stands for term frequency–inverse document frequency. Typically Tf-IDF method is used to assign keywords (words describing the gist of a document) to documents in a corpus of documents.

In our case we will treat users as documents and genres as words.

Term-frequency is given by the following formula:
<center>
$$
    \text{tf}(g, u) = f_{g, u}
$$
</center>
where $f_{g, i}$ is the number of times genre $g$ appear for movies watched by user $u$.

Inverse document frequency is defined as follows:
<center>
$$
    \text{idf}(g) = \log \frac{N}{n_g}
$$
</center>
where $N$ is the number of users and $n_g$ is the number of users with $g$ in their genres list.

Finally, tf-idf is defined as follows:
<center>
$$
    \text{tfidf}(g, u) = \text{tf}(g, u) \cdot \text{idf}(g)
$$
</center>

In our case we will measure how often a given genre appears for movies watched by a given user vs how often it appears for all users. To obtain a movie score we will take the average of its genres' scores for this user.

In [103]:
from sklearn.feature_extraction.text import TfidfVectorizer

class TFIDFRecommender(Recommender):
    """
    Recommender based on the TF-IDF method.
    """
    
    def __init__(self):
        """
        Initialize base recommender params and variables.
        """
        self.tfidf_scores = None
    
    def fit(self, interactions_df, users_df, items_df):
        """
        Training of the recommender.
        
        :param pd.DataFrame interactions_df: DataFrame with recorded interactions between users and items 
            defined by user_id, item_id and features of the interaction.
        :param pd.DataFrame users_df: DataFrame with users and their features defined by user_id and the user feature columns.
        :param pd.DataFrame items_df: DataFrame with items and their features defined by item_id and the item feature columns.
        """
        
        self.tfidf_scores = defaultdict(lambda: 0.0)

        # Prepare the corpus for tfidf calculation
        
        interactions_df = pd.merge(interactions_df, items_df, on='item_id')
#         print("Training set")
#         display(interactions_df.head(10))
#         print()
        user_genres = interactions_df.loc[:, ['user_id', 'genres']]
        user_genres.loc[:, 'genres'] = user_genres['genres'].str.replace("-", "_", regex=False)
        user_genres.loc[:, 'genres'] = user_genres['genres'].str.replace(" ", "_", regex=False)
        user_genres = user_genres.groupby('user_id').aggregate(lambda x: "|".join(x))
        user_genres.loc[:, 'genres'] = user_genres['genres'].str.replace("|", " ", regex=False)
#         print("User genres")
#         display(user_genres.head(10))
#         print()
        user_ids = user_genres.index.tolist()
        genres_corpus = user_genres['genres'].tolist()
#         print("Genres corpus")
#         print(genres_corpus)
#         print()
        
        # Calculate tf-idf scores
        
        vectorizer = TfidfVectorizer()
        tfidf_scores = vectorizer.fit_transform(genres_corpus)
        
        # Transform results into a dict {(user_id, genre): score}
        
        for u in range(tfidf_scores.shape[0]):
            for g in range(tfidf_scores.shape[1]):
                self.tfidf_scores[(user_ids[u], vectorizer.get_feature_names()[g])] = tfidf_scores[u, g]

#         print("TF-IDF scores")
#         print(self.tfidf_scores)
#         print()
    
    def recommend(self, users_df, items_df, n_recommendations=1):
        """
        Serving of recommendations. Scores items in items_df for each user in users_df and returns 
        top n_recommendations for each user.
        
        :param pd.DataFrame users_df: DataFrame with users and their features for which recommendations should be generated.
        :param pd.DataFrame items_df: DataFrame with items and their features which should be scored.
        :param int n_recommendations: Number of recommendations to be returned for each user.
        :return: DataFrame with user_id, item_id and score as columns returning n_recommendations top recommendations 
            for each user.
        :rtype: pd.DataFrame
        """
        
        recommendations = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
        
        # Transform genres to a unified form used by the vectorizer
        
        items_df = items_df.copy()
        items_df.loc[:, 'genres'] = items_df['genres'].str.replace("-", "_", regex=False)
        items_df.loc[:, 'genres'] = items_df['genres'].str.replace(" ", "_", regex=False)
        items_df.loc[:, 'genres'] = items_df['genres'].str.lower()
        items_df.loc[:, 'genres'] = items_df['genres'].str.split("|")
                
        # Score items    
        
        for uix, user in users_df.iterrows():
            items = []
            for iix, item in items_df.iterrows():
                score = 0.0
                for genre in item['genres']:
                    score += self.tfidf_scores[(user['user_id'], genre)]
                score /= len(item['genres'])
                items.append((item['item_id'], score))
                
            items = sorted(items, key=lambda x: x[1], reverse=True)
            user_recommendations = pd.DataFrame({'user_id': user['user_id'],
                                                 'item_id': [item[0] for item in items][:n_recommendations],
                                                 'score': [item[1] for item in items][:n_recommendations]})

            recommendations = pd.concat([recommendations, user_recommendations])

        return recommendations

In [104]:
# Print movies watched by user 1, 2

active_user_movies = ml_df.loc[(ml_df['user_id'] == 1) | (ml_df['user_id'] == 2)]
print("Active users history")
display(active_user_movies)

Active users history


user_id  item_id  rating   timestamp  \
572          1       50     5.0   964982931   
2946         1      423     3.0   964982363   
3790         1      543     4.0   964981179   
5338         1      780     3.0   964984086   
5709         1      940     5.0   964982176   
7753         1     1213     5.0   964982951   
9398         1     1500     4.0   964980985   
10294        1     1777     4.0   964981230   
10520        1     2000     4.0   964982211   
10974        1     2046     4.0   964982563   
11104        1     2078     5.0   964982838   
11401        1     2116     5.0   964982876   
12401        1     2502     5.0   964981278   
13422        1     2692     5.0   964981855   
13573        1     2716     5.0   964983414   
14201        1     2947     5.0   964982176   
15028        1     3053     5.0   964984086   
15039        1     3062     4.0   964981872   
15411        1     3439     4.0   964981799   
15524        1     3479     4.0   964981725   
15867        1     3639     4.0   964982271   
15885        1     3671     5.0   964981589   
16243        1     4006     4.0   964982903   
16613        2     1704     4.5  1445715228   
16885        2     8798     3.5  1445714960   
17605        2    80489     4.5  1445715340   
17777        2    99114     3.5  1445714874   
17975        2   112552     4.0  1445714882   
18016        2   115713     3.5  1445714854   

                                                   title  \
572                           Usual Suspects, The (1995)   
2946                                   Blown Away (1994)   
3790                 So I Married an Axe Murderer (1993)   
5338                Independence Day (a.k.a. ID4) (1996)   
5709                Adventures of Robin Hood, The (1938)   
7753                                   Goodfellas (1990)   
9398                          Grosse Pointe Blank (1997)   
10294                         Wedding Singer, The (1998)   
10520                               Lethal Weapon (1987)   
10974                     Flight of the Navigator (1986)   
11104                            Jungle Book, The (1967)   
11401                      Lord of the Rings, The (1978)   
12401                                Office Space (1999)   
13422                   Run Lola Run (Lola rennt) (1998)   
13573         Ghostbusters (a.k.a. Ghost Busters) (1984)   
14201                                  Goldfinger (1964)   
15028    Messenger: The Story of Joan of Arc, The (1999)   
15039                            Longest Day, The (1962)   
15411  Teenage Mutant Ninja Turtles II: The Secret of...   
15524                                   Ladyhawke (1985)   
15867                Man with the Golden Gun, The (1974)   
15885                             Blazing Saddles (1974)   
16243                     Transformers: The Movie (1986)   
16613                           Good Will Hunting (1997)   
16885                                  Collateral (2004)   
17605                                   Town, The (2010)   
17777                            Django Unchained (2012)   
17975                                    Whiplash (2014)   
18016                                  Ex Machina (2015)   

                                     genres  
572                  Crime|Mystery|Thriller  
2946                        Action|Thriller  
3790                Comedy|Romance|Thriller  
5338       Action|Adventure|Sci-Fi|Thriller  
5709               Action|Adventure|Romance  
7753                            Crime|Drama  
9398                   Comedy|Crime|Romance  
10294                        Comedy|Romance  
10520             Action|Comedy|Crime|Drama  
10974             Adventure|Children|Sci-Fi  
11104     Animation|Children|Comedy|Musical  
11401  Adventure|Animation|Children|Fantasy  
12401                          Comedy|Crime  
13422                          Action|Crime  
13573                  Action|Comedy|Sci-Fi  
14201             Action|Adventure|Thriller  
15028        

In [105]:
# Quick test of the recommender

tfidf_recommender = TFIDFRecommender()
tfidf_recommender.fit(ml_ratings_df, None, ml_movies_df)
recommendations = tfidf_recommender.recommend(pd.DataFrame([[1], [2]], columns=['user_id']), ml_movies_df, 10)

recommendations = pd.merge(recommendations, ml_movies_df, on='item_id', how='left')
print("Recommendations")
display(recommendations)

Recommendations


user_id item_id     score  \
0        1    2534  0.453064   
1        1    4441  0.453064   
2        1    4630  0.453064   
3        1    4947  0.453064   
4        1    5155  0.453064   
5        1    5212  0.453064   
6        1    7192  0.453064   
7        1   63276  0.453064   
8        1     809  0.423382   
9        1   56775  0.423382   
10       2     193  0.757640   
11       2     219  0.757640   
12       2     233  0.757640   
13       2     279  0.757640   
14       2     337  0.757640   
15       2     406  0.757640   
16       2     475  0.757640   
17       2     636  0.757640   
18       2     668  0.757640   
19       2     670  0.757640   

                                               title            genres  
0                                   Avalanche (1978)            Action  
1                               Game of Death (1978)            Action  
2                             No Holds Barred (1989)            Action  
3                               Gauntlet, The (1977)            Action  
4                          Big Bird Cage, The (1972)            Action  
5                                Octagon, The (1980)            Action  
6                             Only the Strong (1993)            Action  
7                    Crows Zero (Kurôzu zero) (2007)            Action  
8                                        Fled (1996)  Action|Adventure  
9          National Treasure: Book of Secrets (2007)  Action|Adventure  
10                                  Showgirls (1995)             Drama  
11                                  Cure, The (1995)             Drama  
12                                    Exotica (1994)             Drama  
13                                  My Family (1995)             Drama  
14                What's Eating Gilbert Grape (1993)             Drama  
15                               Federal Hill (1994)             Drama  
16                  In the Name of the Father (1993)             Drama  
17                                      Frisk (1995)             Drama  
18  Song of the Little Road (Pather Panchali) (1955)             Drama  
19            World of Apu, The (Apur Sansar) (1959)             Drama

### Train-test split test

In [99]:
tfidf_recommender = TFIDFRecommender()

t0 = time.time()

results = [['TFIDFRecommender'] + list(evaluate_train_test_split_implicit(
    tfidf_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id']], ml_movies_df))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))

Recommender      HR@1      HR@3      HR@5    HR@10    NDCG@1  \
0  TFIDFRecommender  0.017897  0.044743  0.058166  0.09396  0.017897   

     NDCG@3    NDCG@5   NDCG@10  
0  0.033077  0.038368  0.049966

Total evaluation time: 42.370760917663574


### Leave-one-out test

In [100]:
tfidf_recommender = TFIDFRecommender()

t0 = time.time()

results = [['TFIDFRecommender'] + list(evaluate_leave_one_out_implicit(
    tfidf_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id']], ml_movies_df, max_evals=300, seed=6789))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))

Recommender      HR@1      HR@3      HR@5  HR@10    NDCG@1    NDCG@3  \
0  TFIDFRecommender  0.003333  0.006667  0.006667   0.02  0.003333  0.005436   

     NDCG@5   NDCG@10  
0  0.005436  0.009773

Total evaluation time: 122.92426872253418
